In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [39]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn import preprocessing
from sklearn.feature_selection import VarianceThreshold
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import LinearRegression
from xgboost import XGBClassifier
from sklearn.metrics import f1_score
from sklearn.utils import resample
from sklearn.ensemble import RandomForestRegressor
from sklearn import metrics
from sklearn.metrics import mean_squared_error as MSE
import xgboost as xgb


In [9]:
from pydantic_settings import BaseSettings


In [12]:
from ydata_profiling import ProfileReport

df = pd.read_csv('/content/drive/MyDrive/banking -dataset/Train Set.csv')

profile = ProfileReport(df, title="Data Profiling Report", explorative=True)

In [13]:
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [14]:
# Train Data
trainData = pd.read_csv("/content/drive/MyDrive/banking -dataset/Train Set.csv")

# Test Data
testData = pd.read_csv("/content/drive/MyDrive/banking -dataset/Test Set.csv")


# Train and Test Dataset

# loan and housing feature

In [15]:
# Train Data
trainData.drop(trainData[trainData['loan'] == 'unknown'].index, axis=0, inplace=True)
trainData.drop(trainData[trainData['housing'] == 'unknown'].index, axis=0, inplace=True)

# previous feature

In [16]:
# Train Data
trainData.loc[trainData['previous'] > 15, 'previous'] = 1

# fill education feature depinding on job

In [17]:
# Train Data
trainData.loc[(trainData['education'] == 'unknown') & (trainData['job'] == 'management'), 'education'] = 'university.degree'
trainData.loc[(trainData['education'] == 'unknown') & (trainData['job'] == 'services'), 'education'] = 'high.school'
trainData.loc[(trainData['education'] == 'unknown') & (trainData['job'] == 'housemaid'), 'education'] = 'basic.4y'
trainData.loc[(trainData['education'] == 'unknown') & (trainData['job'] == 'entrepreneur'), 'education'] = 'basic.6y'
trainData.loc[(trainData['education'] == 'unknown') & (trainData['job'] == 'unemployed'), 'education'] = 'illiterate'
trainData.loc[(trainData['education'] == 'unknown') & (trainData['job'] == 'blue-collar'), 'education'] = 'professional.course'
trainData.loc[(trainData['education'] == 'unknown') & (trainData['job'] == 'admin'), 'education'] = 'university.degree'
trainData.loc[(trainData['education'] == 'unknown') & (trainData['job'] == 'technician'), 'education'] = 'professional.course'
trainData.loc[(trainData['education'] == 'unknown') & (trainData['job'] == 'self-employed'), 'education'] = 'professional.course'
trainData.loc[(trainData['education'] == 'unknown') & (trainData['job'] == 'student'), 'education'] = 'university.degree'



# Test Data

testData.loc[(testData['education'] == 'unknown') & (testData['job'] == 'management'), 'education'] = 'university.degree'
testData.loc[(testData['education'] == 'unknown') & (testData['job'] == 'services'), 'education'] = 'high.school'
testData.loc[(testData['education'] == 'unknown') & (testData['job'] == 'housemaid'), 'education'] = 'basic.4y'
testData.loc[(testData['education'] == 'unknown') & (testData['job'] == 'entrepreneur'), 'education'] = 'basic.6y'
testData.loc[(testData['education'] == 'unknown') & (testData['job'] == 'unemployed'), 'education'] = 'illiterate'
testData.loc[(testData['education'] == 'unknown') & (testData['job'] == 'blue-collar'), 'education'] = 'professional.course'
testData.loc[(testData['education'] == 'unknown') & (testData['job'] == 'admin'), 'education'] = 'university.degree'
testData.loc[(testData['education'] == 'unknown') & (testData['job'] == 'technician'), 'education'] = 'professional.course'
testData.loc[(testData['education'] == 'unknown') & (testData['job'] == 'self-employed'), 'education'] = 'professional.course'
testData.loc[(testData['education'] == 'unknown') & (testData['job'] == 'student'), 'education'] = 'university.degree'

In [18]:
# Train Data
train_most_frequent_education = trainData['education'].mode().iloc[0]
trainData.loc[trainData['education'] == 'unknown', 'education'] = train_most_frequent_education

# Test Data
test_most_frequent_education = testData['education'].mode().iloc[0]
testData.loc[testData['education'] == 'unknown', 'education'] = test_most_frequent_education

# fill month feature depinding on day

In [19]:
# Train Data
trainData['month'] = trainData['month'].astype(str)
train_days_in_month_column = ['mon','fri','wed','thu','tue']
trainData['month'] = trainData.apply(lambda row: row['day'] if row['month']  in train_days_in_month_column else row['month'], axis=1)

# Test Data
testData['month'] = testData['month'].astype(str)
test_days_in_month_column = ['mon','fri','wed','thu','tue']
testData['month'] = testData.apply(lambda row: row['day'] if row['month']  in test_days_in_month_column else row['month'], axis=1)


# drop useless feature

In [20]:
# Train Data
drop_columns = ['id' , 'day',  'balance']

trainData = trainData.drop(columns = drop_columns)

# Test Data
testData = testData.drop(columns = drop_columns)

In [21]:
# Train Data
trainData.reset_index(drop=True, inplace=True)

# Test Data
testData.reset_index(drop=True, inplace=True)

# fill job feature with mode()

In [22]:
# Train Data
train_most_frequent_job = trainData['job'].mode().iloc[0]
trainData.loc[trainData['job'] == 'unknown', 'job'] = train_most_frequent_job

# Test Data
test_most_frequent_job = testData['job'].mode().iloc[0]
testData.loc[testData['job'] == 'unknown', 'job'] = test_most_frequent_job

# fill marital feature with mode()

In [23]:
# Train Data
train_most_frequent_marital = trainData['marital'].mode().iloc[0]
trainData.loc[trainData['marital'] == 'unknown', 'marital'] = train_most_frequent_marital

# Test Data
test_most_frequent_marital = testData['marital'].mode().iloc[0]
testData.loc[testData['marital'] == 'unknown', 'marital'] = test_most_frequent_marital

# fill default depinding on [education]

In [24]:
# case 2 === > without fill unknown
# case 3 === > fill with mode()

# Train Data
def replace_default(education):
    if education in ['tertiary' , 'secondary' , 'primary']:
        return 'yes'
    else:
        return 'no'

trainData['default'] = trainData['default'].apply(lambda x: replace_default(x) if x == 'unknown' else x)


# Test Data

testData['default'] = testData['default'].apply(lambda x: replace_default(x) if x == 'unknown' else x)

# remove Outliers from campaign

In [25]:
Q1 = trainData['campaign'].quantile(0.25)
Q3 = trainData['campaign'].quantile(0.75)
IQR = Q3-Q1
UPPER = Q3 + 1.5*IQR
trainData = trainData[trainData['campaign'] <= UPPER]
trainData.reset_index(drop=True, inplace=True)

In [26]:
Q1 = trainData['age'].quantile(0.25)
Q3 = trainData['age'].quantile(0.75)
IQR = Q3-Q1
UPPER = Q3 + 1.5*IQR
trainData = trainData[trainData['age'] <= UPPER]
trainData.reset_index(drop=True, inplace=True)

# LabelEncoder

In [27]:
le = preprocessing.LabelEncoder()

In [28]:
trainData[['job' , 'marital' , 'education' , 'default'
           , 'housing' , 'loan' , 'month'
           , 'Target','poutcome','pdays','contact']]=trainData[['job' , 'marital' , 'education' , 'default'
           , 'housing' , 'loan' , 'month' , 'Target','poutcome','pdays','contact']].apply(le.fit_transform)

In [29]:
testData[['job' , 'marital' , 'education' , 'default'
           , 'housing' , 'loan' , 'month','poutcome'
           ,'pdays','contact']]=testData[['job' , 'marital' , 'education' , 'default'
           , 'housing' , 'loan' , 'month','poutcome' ,'pdays','contact']].apply(le.fit_transform)

# Data Resampling Techniques

# over-sampling

In [30]:
# Train Data
# Separate majority and minority classes
majority_class = trainData[trainData['Target'] == 0]
minority_class = trainData[trainData['Target'] == 1]

# Upsample the minority class using resample
upsampled_minority = resample(minority_class, replace=True, n_samples=len(majority_class), random_state=42)

# Combine the upsampled minority class with the majority class
trainData = pd.concat([majority_class, upsampled_minority])

In [31]:
X = trainData.drop('Target', axis=1)
y = trainData['Target']

In [32]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2)

In [35]:
regressor = RandomForestRegressor(n_estimators=20, random_state=0)
regressor.fit(X_train, y_train)


RandomForestRegressor(n_estimators=20, random_state=0)

In [36]:
y_pred = regressor.predict(X_test)

In [37]:
def threshold_to_binary_classes(values, threshold=0.5):
    binary_classes = [1 if value > threshold else 0 for value in values]
    return binary_classes

y_pred = threshold_to_binary_classes(y_pred, threshold=0.5)


In [38]:
f1 = f1_score(y_test, y_pred)

print("F1 Score:", f1)

F1 Score: 0.9658621439443359


In [40]:

XGB = xgb.XGBRegressor(objective ='reg:squarederror', learning_rate = 0.4,
                max_depth = 30, alpha = 5, n_estimators = 200)
XGB.fit(X_train, y_train)
# XGB.fit(X_resampled, y_resampled)

XGBRegressor(alpha=5, base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=None, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=0.4, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=30, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             multi_strategy=None, n_estimators=200, n_jobs=None,
             num_parallel_tree=None, ...)

In [41]:
y_pred = XGB.predict(X_test)
# y_pred = XGB.predict(testData)

In [42]:
def threshold_to_binary_classes(values, threshold=0.5):
    binary_classes = [1 if value > threshold else 0 for value in values]
    return binary_classes

y_pred = threshold_to_binary_classes(y_pred, threshold=0.5)

In [43]:
f1 = f1_score(y_test, y_pred)

print("F1 Score:", f1)

F1 Score: 0.9596970516635109
